<h1>What factors influence Salary the most? Education or Projections of Jobs in the specific field? </h1>

In [2]:
from bs4 import BeautifulSoup
#import requests
import pandas as pd
#from selenium import webdriver
#import time
import matplotlib.pyplot as plt
import seaborn as sns

<h1>Part I: Get Data</h1>

In [3]:
url = "https://money.usnews.com/careers/best-jobs/rankings/the-100-best-jobs/"
#headers = {"User-Agent": "Mozilla/5.0 (X11; CrOS x86_64 12871.102.0) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/81.0.4044.141 Safari/537.36"}
#html = requests.get(url, headers=headers)
#But couldn't simply use request to get the data because the site is dynamic and needed scrolling and clicking to get more data

<h1>Use Selenium to scroll down the page and get all jobs</h1>

<b> Site probably detected automation was used, so hidden data would not appear after scrolling.</b>
<p>I headed to the site below to figure out how to overcome that:</p>
<a href="https://piprogramming.org/articles/How-to-make-Selenium-undetectable-and-stealth--7-Ways-to-hide-your-Bot-Automation-from-Detection-0000000017.html"> 12 Ways to hide your bot automation </a>

In [6]:
option = webdriver.ChromeOptions()

#Removes navigator.webdriver flag
option.add_argument('--disable-blink-features=AutomationControlled')

#Open Browser
driver = webdriver.Chrome(executable_path='chromedriver.exe',options=option)
driver.maximize_window()
driver.get(url)


#Now to the actual Scrolling
pause_time = 10 #Seconds

#Get the length of the page
first_height = driver.execute_script("return document.body.scrollHeight") #"body" can be replaced with "documentElement"
print("Initial Page Length: ", first_height)

def load():
    """Function To Scroll Down"""
    global driver, first_height
    
    #Actual Scrolling command
    driver.execute_script("window.scrollTo(0, document.documentElement.scrollHeight);")
    time.sleep(pause_time) #Give time to load the next chunck
    
    # Calculate new scroll height and compare with last scroll height
    current_height = driver.execute_script("return document.body.scrollHeight")
    print("Current Page Length: ", current_height)
    if current_height == first_height:
        return 0;
    first_height = current_height

#Load Scroll many times
while True:
    load()
        
    if load() == 0: #Load returns 0 when the page height remained unchanged after a new scroll
        print("Hit the bottom!")
        time.sleep(pause_time) #Give time to load next chunk if there is still more
        
        #Now click on the load button to load the remaining data
        try:
            driver.find_elements_by_xpath("//*[text()='Load More']")[0].click() #Click on the Load Button
            print("Load More Button Clicked!\nLoading More Data...")
            load() #Load the next chuncks
        except:
            print("Reached bottom of page, no further data to load.")
            break

Initial Page Length:  4759
Current Page Length:  14765
Current Page Length:  17989
Current Page Length:  17989
Current Page Length:  17989
Hit the bottom!
Load More Button Clicked!
Loading More Data...
Current Page Length:  21237
Current Page Length:  24719
Current Page Length:  27919
Current Page Length:  31119
Current Page Length:  34625
Current Page Length:  34625
Current Page Length:  34625
Hit the bottom!
Reached bottom of page, no further data to load.


In [7]:
soup = BeautifulSoup(driver.page_source, "html.parser")

<h1> Create a dataframe with only column names </h1>
<h2> and then add rows with df.loc[index] = [list of values] for each data entry.</h2>

In [8]:
df = pd.DataFrame(columns=["Title", "Rank", "Projected Jobs", "Median Salary", "Education Needed"])

In [9]:
#All the jobs on the page are contained in a div tag with class = "card-content-container"
jobs = soup.find_all("div", class_="card-content-container")

In [10]:
index = 0

for job in jobs:
    title = job.find("h2").string
    rank = job.span.span.text.lstrip("#")

    data = job.find_all("dd")
    projected_jobs = data[0].a.string;   """Remove comma -->"""; projected_jobs = "".join(projected_jobs.split(","))
    median_salary = data[1].a.string.lstrip("$"); """Remove comma -->"""; median_salary = "".join(median_salary.split(","))
    try:
        education_needed = data[2].a.string
    except Exception:
        education_needed = "Not required"
    
    df.loc[index] = [title, rank, projected_jobs, median_salary, education_needed]
    
    index += 1

In [3]:
#Load df from csv in subsequent runs as the scrapped data has been saved already
df = pd.read_csv("best_jobs_scraped.csv")

In [4]:
df.head(10)

Title  Rank  Projected Jobs  Median Salary  \
0         Information Security Analyst     1           47100         103590   
1                   Nurse Practitioner     2          114900         111680   
2                  Physician Assistant     3           40100         115390   
3  Medical and Health Services Manager     4          139600         104280   
4                   Software Developer     5          409500         110140   
5                       Data Scientist     6           19800          98230   
6                    Financial Manager     7          118200         134180   
7                         Statistician     8           14900          92270   
8                               Lawyer     9           71500         126930   
9          Speech-Language Pathologist    10           45400          80480   

  Education Needed  
0       Bachelor's  
1         Master's  
2         Master's  
3       Bachelor's  
4       Bachelor's  
5       Bachelor's  
6       Bachelor's  
7         Master's  
8        Doctorate  
9         Master's

<h1>Part II: Data Wrangling</h1>

In [5]:
df[["Projected Jobs", "Rank", "Median Salary"]] = df[["Projected Jobs", "Rank", "Median Salary"]].astype(int)
df.dtypes

Title               object
Rank                 int32
Projected Jobs       int32
Median Salary        int32
Education Needed    object
dtype: object

In [22]:
#Save the scrapped data if not saved already
df.to_csv("best_jobs_scraped.csv", index=False)

<h1>Part III: Exploratory Data Analysis</h1>

<b>Basic Descriptive Stats</b>

In [7]:
df.describe()

Rank  Projected Jobs  Median Salary
count  100.000000    1.000000e+02     100.000000
mean    50.470000    7.405600e+04   87453.000000
std     29.023312    1.727143e+05   45534.558094
min      1.000000   -7.000000e+03   24960.000000
25%     25.750000    5.975000e+03   55717.500000
50%     50.500000    2.600000e+04   77145.000000
75%     75.250000    6.407500e+04  106870.000000
max    100.000000    1.129900e+06  208000.000000

In [11]:
#Summarize the categorical variables
educations = df['Education Needed'].value_counts().to_frame()
#How many jobs out of 100 require each category of education

educations

Education Needed
Bachelor's                              38
Doctorate                               16
Master's                                15
High School                             10
Associate's                              8
Postsecondary non-degree                 6
Not required                             5
Some college, no degree                  2

<b>Median Salary is the target variable</b>
<p>Trying to see the relationship between the target and the other variables.</p>

In [6]:
%matplotlib inline

In [14]:
#For categorical variables
#plt.figure(figsize=(40,30))  #But this Changes all figures size settings
sns.set(rc={'figure.figsize':(25, 8), 'figure.dpi':600, 'savefig.dpi':600}, font_scale=1.5, style='whitegrid')
sns.boxplot(x="Education Needed", y="Median Salary", data=df)

<AxesSubplot:xlabel='Education Needed', ylabel='Median Salary'>

Education seems to be a very good indicator

In [15]:
#Scatter Plot for numerical data
plt.scatter(df["Projected Jobs"], df["Median Salary"])
plt.xlabel("Projected Jobs")
plt.ylabel("Median Salary")
plt.show()

<b>Basic Grouping</b>

In [60]:
df['Education Needed'].unique()

array(["Bachelor's", "Master's", 'Doctorate', "Associate's",
       'High School', 'Postsecondary non-degree', 'Not required',
       'Some college, no degree'], dtype=object)

In [65]:
educations_and_salary = df[["Education Needed", "Median Salary"]]
salary_by_education = educations_and_salary.groupby(["Education Needed"], as_index = False).mean()
salary_by_education

Education Needed  Median Salary
0               Associate's   69123.750000
1                Bachelor's   90106.578947
2                 Doctorate  148724.375000
3               High School   42270.000000
4                  Master's   96366.666667
5              Not required   29812.000000
6  Postsecondary non-degree   45826.666667
7   Some college, no degree   48225.000000

In [71]:
educations_and_jobs = df[["Education Needed", "Projected Jobs"]]
jobs_by_education = educations_and_jobs.groupby(["Education Needed"], as_index = False).mean()
jobs_by_education

Education Needed  Projected Jobs
0               Associate's    20475.000000
1                Bachelor's    65131.578947
2                 Doctorate    11487.500000
3               High School   274980.000000
4                  Master's    20453.333333
5              Not required   233700.000000
6  Postsecondary non-degree    47200.000000
7   Some college, no degree    37350.000000

# Correlations

In [23]:
df.corr()

Rank  Projected Jobs  Median Salary
Rank            1.000000       -0.098079      -0.401447
Projected Jobs -0.098079        1.000000      -0.292828
Median Salary  -0.401447       -0.292828       1.000000

In [90]:
sns.regplot(x='Projected Jobs', y='Median Salary', data=df)
plt.ylim(0,)

(0.0, 225266.65840862633)

Poor linear relationship between projected jobs and median salary

In [91]:
sns.regplot(x='Rank', y='Median Salary', data=df)

<AxesSubplot:xlabel='Rank', ylabel='Median Salary'>

The linear relationship for rank and median salary seems good
# Let's check these with correlation coefficient and p-value

In [18]:
from scipy import stats

In [20]:
pearson_coef, p_value = stats.pearsonr(df['Projected Jobs'], df['Median Salary'])
print(pearson_coef)
print(p_value)

-0.2928277149323589
0.0031109321765488323


There is a weak negative correlation between Projected Jobs and Median Salary
and the p-value is between 0.001 and 0.5, therefore we have moderate certainty about the correlation.

In [21]:
pearson_coef1, p_value1 = stats.pearsonr(df['Rank'], df['Median Salary'])
print(pearson_coef1)
print(p_value1)

-0.40144685836506305
3.480281176095211e-05


We have a moderate negative correlation between the rank of the job and the median salary. As the rank increases, the median salary decreases (obviously best jobs score higher and are ranked first). And the p-value is way lower than 0.001, so we have a strong certainty about our correlation.

<h1>Part IV: Model Development</h1>

<h2>Let's Try to predict Median Salary</h2>
<h3>Build Model</h3>

In [24]:
from sklearn.linear_model import LinearRegression

In [35]:
#Simple Linear Regression for relationship between Median Salary and Projected Jobs
lm = LinearRegression()
x = df[["Projected Jobs"]]
y = df[["Median Salary"]]
lm.fit(x, y) #Fit or train the model to get slope and intercept of the linear equation y = b0 +b1x
print(f"yhat = {lm.intercept_[0]}{+1*lm.coef_[0][0]}*x")

yhat = 93170.22496145885-0.07720137411497849*x


In [83]:
#Find R^2 (In-Sample Evaluation)
lm.score(x, y)

0.08574807063250678

In [82]:
#Very Low R^2, not good

In [54]:
#Now we can use our model (yhat) to make predictions
lm.predict([[47100], [114900]])
#Real values are 103,5990 and 111,680

array([[89534.04024064],
       [84299.78707565]])

In [41]:
#Multiple Linear Regression. We do not have a lot of features, so let's use rank
mlm = LinearRegression()
z = df[['Projected Jobs', 'Rank']]
mlm.fit(z, y)
print(f"yhat = {mlm.intercept_[0]}{+1*mlm.coef_[0][0]}*x1{+1*mlm.coef_[0][1]}*x2")

yhat = 128394.36743770968-0.08843252235857449*x1-681.4426106979015*x2


In [87]:
#Find R^2 (In-Sample evaluation)
mlm.score(z, y)

0.2725891369371187

In [86]:
#R^2 Not that bad but still very low

In [52]:
mlm.predict([[47100, 1], [114900, 2]])
#Real values are 103,5990 and 111,680

array([[123547.75302392],
       [116870.58539731]])

<h3>Evaluate Model with Visualization</h3>

In [55]:
#Regression Plot already produced above in correlation section

In [56]:
#Residual plots
sns.residplot(x='Projected Jobs', y='Median Salary', data = df)

<AxesSubplot:xlabel='Projected Jobs', ylabel='Median Salary'>

errors are randomly distributed above and below the mean 0, but clustered on one side of the x axis. Not sure what this should mean at this point in time

In [57]:
sns.residplot(x='Rank', y='Median Salary', data = df)

<AxesSubplot:xlabel='Rank', ylabel='Median Salary'>

Errors are randomly distributed above and below the mean. Model assumption for rank vs Median Salary is correct

In [62]:
#Some troubles using Distribution Plot
#Skipped

<h3>Polynomial Regression</h3>

In [65]:
import numpy as np

In [66]:
#Generate a 3rd order polynomial for Projected Jobs and Median Salary
fn = np.polyfit(df['Projected Jobs'], df['Median Salary'], 3)
p = np.poly1d(fn)
p

poly1d([-7.46296851e-13,  1.21087759e-06, -4.85830658e-01,  1.04965032e+05])

In [67]:
#Regression with more than one dimension(feature)

In [70]:
from sklearn.preprocessing import PolynomialFeatures
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline

In [71]:
input = [('scale', StandardScaler()), ('polynomial', PolynomialFeatures(degree=2)), ('mode', LinearRegression())]
pipe = Pipeline(input)

In [72]:
pipe.fit(df[['Projected Jobs', 'Rank']], y)

Pipeline(steps=[('scale', StandardScaler()),
                ('polynomial', PolynomialFeatures()),
                ('mode', LinearRegression())])

In [73]:
pipe.predict([[47100, 1], [114900, 2]])
#Real values are 103,5990 and 111,680

array([[124209.19702159],
       [108304.59128589]])

<h2>In-Sample Evaluation</h2>
<p>How good our models fit the data</p>

In [74]:
from sklearn.metrics import mean_squared_error

In [77]:
#Takes actual value and predicted value
mean_squared_error(df[['Median Salary']], lm.predict(df[['Projected Jobs']]))

1876650213.0386279

In [88]:
mean_squared_error(df['Median Salary'], pipe.predict(df[['Projected Jobs', 'Rank']]))

1372916381.8105798

In [90]:
#R^2, done above in Model Development